![atlas](atlas4.png)

A fire atlas is a configuration convention for geospatial assets related to community fire planning and response together with a configuration for ways to instantiate, edit, and manage those assets.

A stewardship atlas is a data set, a confuration for storing, processing, and sharing that data set, and a set of implementions to do so.

In [23]:
# Boring Imports
import sys, os, subprocess, time, json, string, datetime, random, math
import geojson
import h3
sys.path.insert(0, "/root/stewardship_atlas/python")

# our Imports
import json_config
import dataswale_geojson
import dataswale_geojson as dataswale

import deltas_geojson as deltas
import versioning
import vector_inlets
import raster_inlets
import outlets
import atlas
import utils
import eddies


# Create a new atlas from GeoJSON

In [ ]:
{l['name']:l for l in layers}['burns_index']['fill_opacity'] = ['get', 'haul_normalized']

ld={l['name']:l for l in layers}

ld['burns_index']['fill_opacity'] = ['get', 'haul_normalized']
ld['burns_index']

layers[9]

In [76]:
gj = {
  "type": "FeatureCollection",
  "features": [
    {
      "type": "Feature",
      "properties": {
          "name": "mineralkinsey", 
          "logo": "https://img1.wsimg.com/isteam/ip/11ac4488-96b5-4627-b850-ebbe7cdd6cf8/logo.png"},
      "geometry": {
        "coordinates": [ utils.bbox_to_polygon({
            "south": 40.18,
            "north": 40.21,
            "west": -123.95,
            "east": -123.9
            
        })],
        "type": "Polygon"
      }}]}

layers = json.load(open("../configuration/MineralKinsey_layers.json"))
assets = json.load(open("../configuration/MineralKinsey_assets.json"))

# hack in a layer config change here
{l['name']:l for l in layers}['burns_index']['fill_opacity'] = ['get', 'haul_normalized']
#{l['name']:l for l in layers}['burns_index']['fill_opacity'] = 0.1

c = atlas.create(feature_collection=gj, layers=layers, assets=assets)

Updating password for user internal
Updating password for user admin
Updating password for user admin
Updating password for user internal
Updating password for user admin
Updating password for user admin
Updating password for user admin
Updating password for user internal
Updating password for user admin
Updating password for user admin
Updating password for user admin
2025-10-01 08:26:43,661 - atlas - INFO - Storing initial feature collection in {p /'layers' / 'regions'}...
2025-10-01 08:26:43,662 - atlas - INFO - built a config for mineralkinsey.


In [97]:
{l['name']:l for l in c['dataswale']['layers']}['burns_index']

{'name': 'burns_index',
 'geometry_type': 'polygon',
 'color': [0, 0, 0],
 'fill_color': [200, 55, 55],
 'fill_opacity': ['get', 'haul_normalized'],
 'add_labels': True,
 'access': ['internal', 'public', 'admin']}

In [ ]:
[x['name'] for x in c['dataswale']['layers']]

### Or use an existing swale and config:

In [ ]:
c = json.load(open("/root/swales/scvfd/staging/atlas_config.json"))


# New School

### Elevation and Hillshade rasters and vectors

In [ ]:
# Lidar hillshade
raster_inlets.local_raster(config=c, name="local_hillshade", delta_queue=deltas)
dataswale_geojson.refresh_raster_layer(c, 'lidar_basemap', deltas.apply_deltas)

In [ ]:
# Still need DEM for contours - make `elevation` layer, then eddy maps:
# * derived_hillshade: elevation -> basemap 
# * gdal_contours: elevation -> contours
raster_inlets.url_raster(config=c, name="dem", delta_queue=deltas)
dataswale_geojson.refresh_raster_layer(c, 'elevation', deltas.apply_deltas)

In [ ]:
dataswale_geojson.eddy(c, 'gdal_contours')

In [ ]:
dataswale_geojson.eddy(c, 'derived_hillshade')

### Core vector layers

In [ ]:
# vector_inlets.overture_duckdb(config=c, name="public_roads", delta_queue=deltas)
atlas.materialize(materializers, c, 'public_roads')
dataswale_geojson.refresh_vector_layer(c, 'roads', delta_queue_builder=deltas.apply_deltas_overwrite)

In [ ]:
# vector_inlets.local_ogr(config=c, name="public_creeks", delta_queue=deltas)
atlas.materialize(materializers, c, 'public_creeks')

dataswale_geojson.refresh_vector_layer(c, 'creeks', delta_queue_builder=deltas.apply_deltas_overwrite)

In [ ]:
c['assets'].keys()

In [ ]:
# vector_inlets.local_ogr(config=c, name="local_milemarkers", delta_queue=deltas)
atlas.materialize(materializers, c, 'local_burns')

In [4]:
dataswale_geojson.refresh_vector_layer(c, 'burns', deltas.apply_deltas)

2025-10-01 03:50:04,133 - deltas_geojson - INFO - Starting Apply Deltas: /root/swales/mineralkinsey/staging/deltas/burns: [PosixPath('/root/swales/mineralkinsey/staging/deltas/burns/assetless__20250728_074608__create.geojson')] -> /root/swales/mineralkinsey/staging/deltas/burns/work
2025-10-01 03:50:04,133 - deltas_geojson - INFO - delta file /root/swales/mineralkinsey/staging/deltas/burns/assetless__20250728_074608__create.geojson
2025-10-01 03:50:04,134 - deltas_geojson - INFO - delta file /root/swales/mineralkinsey/staging/deltas/burns/assetless__20250728_074608__create.geojson: assetless @ 20250728_074608 -> create
2025-10-01 03:50:04,134 - deltas_geojson - INFO - delta file /root/swales/mineralkinsey/staging/deltas/burns/assetless__20250728_074608__create.geojson: assetless @ 20250728_074608 -> create
2025-10-01 03:50:04,142 - deltas_geojson - INFO - moving consumed delta: /root/swales/mineralkinsey/staging/deltas/burns/assetless__20250728_074608__create.geojson -> /root/swales/mi

PosixPath('/root/swales/mineralkinsey/staging/layers/burns/burns.geojson')

### Buildings, Parcels, and Addresses

In [ ]:
vector_inlets.overture_duckdb(config=c, name="public_buildings", delta_queue=deltas)

dataswale_geojson.refresh_vector_layer(c, 'buildings', delta_queue_builder=deltas.apply_deltas_overwrite)

#### First load parcel layer from OpenAddresses

In [ ]:
vector_inlets.local_ogr(config=c, name="oa_parcels", delta_queue=deltas)

dataswale_geojson.refresh_vector_layer(c, 'parcels', deltas.apply_deltas_overwrite)

#### Then get addresses from Oveture - as a Delta to annotate parcels

In [ ]:
vector_inlets.overture_duckdb(config=c, name="public_addresses", delta_queue=deltas)

In [ ]:
eddies.delta_annotate_spatial_duckdb(c, "parcels", "public_addresses__20250703_161745__create")

In [ ]:
# No need to run this since the above annoation updates the layer
dataswale_geojson.refresh_vector_layer(c, 'parcels', deltas.apply_deltas)

#### Now use parcel layer as annotation for Buildings

In [ ]:
eddies.delta_annotate_spatial_duckdb(c, "buildings", "parcels", anno_type="layers")

### POI etc

In [ ]:
atlas.materialize(c, 'public_poi')

In [ ]:
dataswale_geojson.refresh_vector_layer(c, 'natural')

In [ ]:
vector_inlets.local_ogr(config=c, name="local_ponds", delta_queue=deltas)

In [ ]:
dataswale_geojson.refresh_vector_layer(c, 'ponds', deltas.apply_deltas)

In [ ]:
vector_inlets.local_ogr(config=c, name="local_hydrants", delta_queue=deltas)

In [ ]:
dataswale_geojson.refresh_vector_layer(c, 'hydrants', deltas.apply_deltas)

In [ ]:
vector_inlets.local_ogr(config=c, name="local_creeks", delta_queue=deltas)

In [ ]:
dataswale_geojson.refresh_vector_layer(c, 'creeks', deltas.apply_deltas)

In [ ]:
vector_inlets.local_ogr(config=c, name="local_helilandings", delta_queue=deltas)

In [ ]:
dataswale_geojson.refresh_vector_layer(c, 'helilandings', deltas.apply_deltas)

In [5]:
eddies.h3_cells(c, 'burns_h3')

eddies - INFO - Processing H3 cells for layer 'burns' with resolution 11, algorithm 'max_num_cells', max_cells 10
eddies - INFO - Layer 'burns' has geometry type: polygon
eddies - INFO - Processing 26 features in layer 'burns'
eddies - INFO - Indexing Geom Polygon): 1 coords, got {'cells': ['8a28062ca09ffff', '8a28062ca44ffff'], 'resolution': 10, 'cell_count': 2, 'representative_index': '8a28062ca09ffff'}
eddies - DEBUG - FeatureConv 0: Created 2 hexagonal features
eddies - INFO - Indexing Geom Polygon): 1 coords, got {'cells': ['8a28062ca727fff', '8a28062ca737fff'], 'resolution': 10, 'cell_count': 2, 'representative_index': '8a28062ca727fff'}
eddies - DEBUG - FeatureConv 1: Created 4 hexagonal features
eddies - INFO - Indexing Geom Polygon): 1 coords, got {'cells': ['8b28062ca455fff', '8b28062ca454fff', '8b28062ca46afff', '8b28062ca443fff', '8b28062ca442fff', '8b28062ca441fff'], 'resolution': 11, 'cell_count': 6, 'representative_index': '8b28062ca455fff'}
eddies - DEBUG - FeatureConv 

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-123.91548707659294, 40.1945754539544],
      [-123.91484666849144, 40.19508203005226],
      [-123.91506617872858, 40.19573087055399],
      [-123.91592610379338, 40.19587313118643],
      [-123.91656650664571, 40.19536655299783],
      [-123.9163469896826, 40.19471771626753]]]},
   'properties': {'fid': 1,
    'UnitNum': -1,
    'Description': 'SlopeInt',
    'GroundFuels': 1,
    'Comments': None,
    'area': 25361.48944208026,
    'h3_index': '8a28062ca09ffff',
    'h3_resolution': 10,
    'h3_cell_count': 2,
    'source_feature_id': 0}},
  {'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-123.91356582399014, 40.19609517134003],
      [-123.91292538759028, 40.19660173652942],
      [-123.91314489155089, 40.197250574712925],
      [-123.91400483863839, 40.19739284393607],
      [-123.91464526978976, 40.196886276655825],
      [-123.9144

In [ ]:
dataswale_geojson.refresh_document_layer(c, 'documents')

In [ ]:
from pathlib import Path
p=Path('/food/bars/baths/ninja.tif')

In [ ]:
p.suffix

### outlets

In [98]:
outlets.outlet_webmap(c, 'webmap')


2025-10-01 08:57:22,463 - outlets - INFO - Generated sprites with 2 icons: /root/swales/mineralkinsey/staging/outlets/webmap/sprite.png and /root/swales/mineralkinsey/staging/outlets/webmap/sprite@2x.png
2025-10-01 08:57:22,464 - outlets - INFO - Sprite 1x JSON content: {
  "hydrants": {
    "width": 32,
    "height": 32,
    "x": 0,
    "y": 0,
    "pixelRatio": 1
  },
  "natural": {
    "width": 32,
    "height": 32,
    "x": 33,
    "y": 0,
    "pixelRatio": 1
  }
}
2025-10-01 08:57:22,529 - outlets - INFO - Sprite 2x JSON content: {
  "hydrants": {
    "width": 64,
    "height": 64,
    "x": 0,
    "y": 0,
    "pixelRatio": 2
  },
  "natural": {
    "width": 64,
    "height": 64,
    "x": 65,
    "y": 0,
    "pixelRatio": 2
  }
}
2025-10-01 08:57:22,609 - outlets - INFO - In webedit, got Outlet Conf: {'type': 'outlet', 'name': 'webmap', 'in_layers': ['lidar_basemap', 'parcels', 'contours', 'roads', 'creeks', 'buildings', 'natural', 'burns', 'burns_index', 'creeks_index', 'roads_ind

PosixPath('/root/swales/mineralkinsey/staging/outlets/webmap/index.html')

In [ ]:
c['assets']['webmap']

In [ ]:
c['dataswale']['layers']

In [ ]:
outlets.outlet_webmap(c, 'webmap')

In [ ]:
eddies.h3_cells(c, 'burns', 'burns')

# Messing About

## H3

``` 
dataswale.clear_vector_layer(c, 'burns')
```

In [10]:
burns_index = dataswale.layer_as_featurecollection(c, 'burns_index')
creeks_index = dataswale.layer_as_featurecollection(c, 'creeks_index')
# burns = dataswale.layer_as_featurecollection(c, 'burns')

roads_index = dataswale.layer_as_featurecollection(c, 'roads_index')

print(f"Loaded H3 Index layers: burns: {len(burns_index['features'])} " +
      f" creeks: {len(creeks_index['features'])} " +
      f"roads: {len(roads_index['features'])} ")
                                           

Loaded H3 Index layers: burns: 110  creeks: 1270 roads: 492 


In [ ]:
burn_cells = [b["properties"]["h3_index"]
              for b in burns_index['features']]
creek_cells = [b["properties"]["h3_index"]
              for b in creeks_index['features']]
road_cells = [b["properties"]["h3_index"]
              for b in roads_index['features']]

In [26]:
len(creeks_index['features'])

1270

In [ ]:
def match_resolution_at_centers(cell1, cell2):
    target, c,d = None, None, None
    if cell1['properties']['h3_resolution'] < cell2['properties']['h3_resolution']:
        target = cell2['properties']['h3_resolution']
        c = cell1
        d = cell2
    elif cell1['properties']['h3_resolution'] > cell2['properties']['h3_resolution']:
        target = cell1['properties']['h3_resolution']
        c = cell2
        d = cell1
    else:
        print("Already EQUAL")
        target = cell1['properties']['h3_resolution']
        c = cell1
        d = cell2
        
    while c['properties']['h3_resolution'] < target:
        c['properties']['h3_resolution'] += 1
        c['properties']['h3_index'] = h3.cell_to_center_child(c['properties']['h3_index'])
    return cell1, cell2
    

In [35]:

#results = []

def get_cell_path_distances(c, burns_index, creeks_index, distance_name):
    """
    For each H3 cell in `from_layer`, get the min H3 path to everything in `to_layer`
    at the minimum common resolution.
    """
    layer_dict = {l['name']:l for l in c['dataswale']['layers']}
    
    results = []
    for burn in burns_index['features']:
        distances = []
        burn_h3 = burn['properties']['h3_index']
        burn_h3_res = burn['properties']['h3_resolution']
        for creek in creeks_index['features']:
            creek_h3 = creek['properties']['h3_index']
            #burn_h3_center = h3.cell_to_center_child(burn_h3)
            #old_burn = burn.copy()
            burn, creek = match_resolution_at_centers(burn, creek)
            print(f"{burn_h3} [{burn_h3_res}] -> " +
                  f"{burn['properties']['h3_index']} [{burn['properties']['h3_resolution']}] -> " +
                  f"{creek_h3} [{burn['properties']['h3_resolution']}]")
            try:
                d = h3.grid_distance(burn['properties']['h3_index'], creek_h3)
                distances.append(d)
            except Exception as e:
                # h3.grid_distance raises if resolution mismatch or invalid path
                print(f"Problem {e}: {burn['properties']['h3_resolution']} -> " +
                      f"{creek['properties']['h3_resolution']}")
                continue
        if distances:
            min_d = min(distances)
        else:
            min_d = None
        burn['properties'][distance_name] = min_d
        #burn['properties']['name'] = str(min_d)
        results.append({
            #"burn_id": burn_id,
            "burn_h3": burn_h3,
            "min_h3_steps": min_d
    })
    return burns_index

In [113]:
def merge_distances(c, layer_index, dist1, dist2, new_distance):
    distances = {dist1:[], dist2:[], new_distance:[]}
    for feat in layer_index['features']:
        f = feat['properties']
        f[new_distance] = f[dist1] + f[dist2]
        
        distances[dist1].append(f[dist1])
        distances[dist2].append(f[dist2])
        distances[new_distance].append(f[new_distance])
        
    maxes = {
        dist1: max(distances[dist1]),
        dist2 : max(distances[dist2]),
        new_distance : max(distances[new_distance])}
    
    for feat in layer_index['features']:
        for d in [dist1, dist2, new_distance]:
             feat['properties'][f"{d}_normalized"] = \
                float(feat['properties'][d])/float(maxes[d])
        feat['properties']['name'] = ""
            #f"{feat['properties']['creek_distance_normalized']:.2f} {feat['properties']['haul_normalized']:.2f}" 
    #max_dist = max(distances)
    
    return layer_index


In [36]:
burns_index = get_cell_path_distances(c, burns_index, roads_index, 'roads_distance')

8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c8599fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c8591fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c85abfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c8598fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c859afff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c8436fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c858cfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c859dfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c859cfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c8581fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c859efff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c84a6fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c859bfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062c8590fff [11]
8b28062ca098fff [11] -> 8b28062ca0

8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28029649a3fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca65bfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca6ecfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28029649a6fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca652fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca65afff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28029649a0fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28029649a4fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca6edfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca656fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca61bfff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca619fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca690fff [11]
8b28062ca098fff [11] -> 8b28062ca098fff [11] -> 8b28062ca681fff [11]
8b28062ca098fff [11] -> 8b28062ca0

8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28062ca656fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28062ca654fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28062ca646fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28029649a3fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28029649a8fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28029649adfff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28029649aefff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b2802964982fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28029649a3fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b2802964980fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b2802964984fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28062ca60bfff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28062ca609fff [11]
8b28062ca448fff [11] -> 8b28062ca448fff [11] -> 8b28062ca672fff [11]
8b28062ca448fff [11] -> 8b28062ca4

8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca4acfff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca4c9fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca4b4fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062d994dfff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca4b0fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca796fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062d9b60fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca4a9fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062d9b65fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca4e2fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca640fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca645fff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca66afff [11]
8b28062ca720fff [11] -> 8b28062ca720fff [11] -> 8b28062ca29bfff [11]
8b28062ca720fff [11] -> 8b28062ca7

8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac65fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac46fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac45fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac66fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac63fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac44fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac46fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac62fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac44fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac66fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062cac46fff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062dda6bfff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062ce69afff [11]
8b28062ca454fff [11] -> 8b28062ca454fff [11] -> 8b28062dda69fff [11]
8b28062ca454fff [11] -> 8b28062ca4

...

8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9ab6fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a46fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9af4fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a40fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9ab1fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a85fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9aa9fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a18fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a45fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a54fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a6cfff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a6efff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a48fff [11]
8b28062caaf0fff [11] -> 8b28062caaf0fff [11] -> 8b28062d9a49fff [11]
8b28062caaf0fff [11] -> 8b28062caa

8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964870fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b28062cb48bfff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b280296482afff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b280296482dfff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964815fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964801fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b280296480afff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964863fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964811fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b280296480efff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964869fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b2802964818fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b28062cb489fff [11]
8b28062caae8fff [11] -> 8b28062caae8fff [11] -> 8b280296495afff [11]
8b28062caae8fff [11] -> 8b28062caa

8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062cb4e3fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28029648a4fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b2802964861fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062cb4e1fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b2802964814fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062cb4f3fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b2802964871fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b2802964828fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b280296481dfff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b2802964876fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062cac6afff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062cac44fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062cac68fff [11]
8b28062caaa8fff [11] -> 8b28062caaa8fff [11] -> 8b28062ca892fff [11]
8b28062caaa8fff [11] -> 8b28062caa

8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b2802964828fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b280296481dfff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b2802964876fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac6afff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac44fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac68fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062ca892fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac64fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac6cfff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac65fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac46fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac45fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac66fff [11]
8b28062caab0fff [11] -> 8b28062caab0fff [11] -> 8b28062cac63fff [11]
8b28062caab0fff [11] -> 8b28062caa

NameError: name 'burns' is not defined

### Generate new distance from old distances

In [114]:
burns_index =  merge_distances(c, burns_index, 'roads_distance', 'creek_distance', 'haul')

In [115]:
burns_index['features'][3]['properties']

{'fid': 2,
 'UnitNum': 2,
 'Description': 'terrace1',
 'GroundFuels': 1,
 'Comments': None,
 'area': 25818.134565376677,
 'h3_index': '8b28062ca730fff',
 'h3_resolution': 11,
 'h3_cell_count': 2,
 'source_feature_id': 1,
 'creek_distance': 4,
 'name': '',
 'roads_distance': 3,
 'work': 7,
 'haul': 7,
 'haul_normalized': 0.3684210526315789,
 'roads_distance_normalized': 0.2,
 'creek_distance_normalized': 0.5714285714285714}

### Save modified layer

In [116]:
file_path = dataswale.layer_as_path(c,'burns_index')

fc = geojson.FeatureCollection(0)
fc['features'] = burns_index['features']
                                       
with open(file_path, 'w') as f:
    geojson.dump(fc, f)

# Creek Detail Exploration
    

In [119]:
creeks = dataswale.layer_as_featurecollection(c, 'creeks')

In [121]:
import geopandas
gpd = geopandas.GeoDataFrame(creeks['features'])

In [131]:
from collections import Counter 
ctr = Counter([p['properties']['fcode_description'] for p in creeks['features']])

In [132]:
ctr

Counter({'Stream/River: Hydrographic Category = Intermittent': 32,
         'Stream/River: Hydrographic Category = Ephemeral': 35,
         'Artificial Path': 3,
         'Stream/River: Hydrographic Category = Perennial': 14})

In [128]:
gpd.properties

0     {'permanent_identifier': '121523679', 'fdate':...
1     {'permanent_identifier': '{A0D8EBF9-6D4F-492E-...
2     {'permanent_identifier': '{AD250E98-1FAB-4C9E-...
3     {'permanent_identifier': '121523655', 'fdate':...
4     {'permanent_identifier': '{EB8F8621-5032-42C8-...
                            ...                        
79    {'permanent_identifier': '121429025', 'fdate':...
80    {'permanent_identifier': '121428992', 'fdate':...
81    {'permanent_identifier': '121428991', 'fdate':...
82    {'permanent_identifier': '121429002', 'fdate':...
83    {'permanent_identifier': '121429034', 'fdate':...
Name: properties, Length: 84, dtype: object

In [ ]:
burn_cells = [(b["properties"].get("id", i), b["properties"]["h3_index"]) 
              for i, b in enumerate(burns_index)]

In [ ]:
import h3 
pc=[[b,a] for a,b in bc[0]['geometry']['coordinates'][0]]
hs=h3.LatLngPoly(pc)   

In [ ]:
h3.h3shape_to_cells(hs,11)

In [ ]:
versioning.publish_new_version(c)

In [ ]:
import gspread
gc = gspread.service_account()

In [ ]:

ss = gc.open("scvfd Fire Atlas: poi")
wks = ss.sheet1

In [ ]:
ss.url

In [ ]:
features = wks.get_all_records()
features

In [ ]:
s="""{"version_string": "staging", "versions": ["published"], "logo": "/local/scs-smallgrass1.png", "swaleName": "westport", "consoleType": "INTERNAL", "interfaces": [{"type": "outlet", "in_layers": ["basemap", "parcels", "contours", "roads", "internal_roads", "turnouts", "milemarkers", "creeks", "buildings", "helilandings", "hydran\
ts"], "config_def": "webmap", "access": ["internal", "admin"], "config": {"asset_type": "outlet", "name": "webmap", "fetch_type": "webmap", "interaction": "interface", "attribu\
tion": {"url": "https://portal.opentopography.org/api/terms", "description": "Open Topography's Global DEM", "license": "https://portal.opentopography.org/api/terms", "citation\
": "https://portal.opentopography.org/api/terms"}}}, {"type": "outlet", "name": "runbook", "in_layers": ["lidar_basemap", "tsunami", "contours", "roads", "creeks", "buildings",\
 "campgrounds", "helilandings", "milemarkers", "hydrants"], "access": ["internal", "admin"], "config_def": "runbook", "regions": [{"bbox": {"east": -121.19978063408502, "west":\
 -121.20391109005016, "south": 39.23863749098538, "north": 39.24416744687048}, "name": "RockLoop", "caption": "Double loop with Ginger and big rocks.", "vectors": [], "raster":\
 "", "text": "Hwy20 to the County Lnie"}, {"bbox": {"east": -121.19978063408502, "west": -121.20391109005016, "south": 39.23863749098538, "north": 39.24416744687048}, "name": "\
GolfCourses", "caption": "Golf Courses", "vectors": [], "raster": "", "text": "Golf Courses"}], "config": {"asset_type": "outlet", "layers": ["hillshade", "contours", "creeks",\
 "tsunami", "buildings", "helilanding", "overture_roads"], "fetch_type": "runbook", "interaction": "interface", "data_type": "html", "outpath_template": "/runbook/{name}_page_{\
i}.html", "page_name_template": "{name}_page_{i}", "attribution": {"url": "https://www.scvfd.fireatlas.org", "description": "Runbook of the atlas, a linked set of specific subm\
ap/diagram pages.", "license": "https://www.scvfd.fireatlas.org", "citation": "https://www.scvfd.fireatlas.org"}}}], "downloads": [], "useCases": [{"name": "Firefighter", "case\
s": ["Download Avenza version", "Share a QR Code for Avenza", "Mark an Incident", "Mark a POI"]}, {"name": "GIS Practitioner", "cases": ["Download Layer GeoJSON", "Download Geo\
PKG", "Add a layer as GeoJSON"]}, {"name": "Administrator", "cases": ["Go to Admin interface", "Switch Version"]}], "layers": []}"""
print(json.dumps(json.loads(s)['interfaces'], indent=2))

In [ ]:
[].count('d')

In [ ]:
def canonicalize_name(s):
    return "_".join(s.lower().split()).strip()

In [ ]:
canonicalize_name("    h    IU H8  hdh")

In [ ]:
#json.dump(hmm, open("newregions.json", "w"))
regions = json.load( open("newregions.json"))

In [ ]:
utils.geojson_to_bbox([
            [
              -121.19978063408502,
              39.24416744687048
            ],
            [
              -121.20391109005016,
              39.24416744687048
            ],
            [
              -121.20391109005016,
              39.23863749098538
            ],
            [
              -121.19978063408502,
              39.23863749098538
            ],
            [
              -121.19978063408502,
              39.24416744687048
            ]
          ])

In [ ]:
regions[9]['vectors'][-1][0]=ac['assets']['overture_roads']


In [ ]:
atlas_outlets.build_region_map('/root/data/', 'westport', 'stage', 'runbook', regions[9])

In [ ]:
"DFDf".lower()

In [ ]:
hmm = atlas.asset_materialize(ac, dc, ac['assets']['webmap_public'])

In [ ]:
z=json.load(open("zones.geojson"))

In [ ]:
z

In [ ]:
ac['assets'].keys()

In [ ]:
regions[1]['vectors'][0][0]['color']=[0,255,0]

In [ ]:
del(regions[1]['vectors'][0])

In [ ]:
regions[0][1]['raster'] = [ac['assets']['hillshade'], '/root/data/scvfd/stage/staging/hillshade_1_A.tiff']

In [ ]:
atlas_outlets.build_region_map('/root/data/', 'westport', 'stage', '', regions[1])

In [ ]:
#ht5#.format(ea=ac['assets']['creeky'],**ac['assets']['creeky'])
ht1.format(name=ac['assets']['creeky']['name'])
#ac['assets']['creeky']

In [ ]:
import planetary_computer

In [ ]:
dir(planetary_computer)

In [ ]:
for i in range(10) if i %% 3:
    print(i)
    

In [ ]:
j = json.load(open('/root/data/scvfd/staging/roads.geojson'))

from collections import Counter
c=Counter()
for f in j['features']:
    
    c.update(f['properties'].keys())

regions = atlas.asset_materialize(ac, dc, ac['assets']['gazetteer'])

import atlas_outlets
atlas_outlets.export_region_layer_raster('/root/data/', 'scvfd', 'hillshade', regions[0])

In [ ]:
outlets.sql_query(c, 'sqldb', 
                  f"""SELECT column_name 
                  FROM information_schema.columns 
                  WHERE table_name = 'creeks';""")

In [ ]:
regions = atlas_outlets.generate_regions(dc, ac['assets']['gazetteer'])

region_json = json.dump(regions,open('regions_scvfd.json', 'w'))

import atlas_eddies
atlas_eddies.generate_contours('/root/data/scvfd/stage/staging/dem.tiff', '/root/data/scvfd/stage/staging/')

# Queries and DuckDB

In [ ]:
import duckdb
duckdb.sql("""                                                                                                                   
INSTALL spatial;                                                                                                                     
LOAD spatial;                                                                                                                        
""")


In [ ]:
#duckdb.sql("SELECT * FROM duckdb_settings()")
duckdb.sql("SHOW TABLES")

In [ ]:
duckdb.sql("SET s3_region='us-west-2'; DROP TABLE IF EXISTS addresses; CREATE TABLE addresses AS SELECT  * EXCLUDE geometry, ST_AsGeoJSON(ST_GeomFromWKB(geometry)) as geom FROM   read_parquet('s3://overturemaps-us-west-2/release/2025-04-23.0/theme=addresses/type=*/*', filename=true, hive_partitioning=1) WHERE  bbox.xmin > -123.85333388805361  AND bbox.xmax < -123.67763908625702  AND bbox.ymin > 39.53857292439969  AND bbox.ymax < 39.89595306214338  AND street != 'NONE';")

In [ ]:
# (min_x DOUBLE, min_y DOUBLE, ma
obq = """
SET s3_region='us-west-2';

SELECT
  * EXCLUDE geometry, -- ST_GeomFromWKB(geometry) as geom,
FROM
  read_parquet('s3://overturemaps-us-west-2/release/2025-04-23.0/theme=buildings/type=building/*', filename=true, hive_partitioning=1)
WHERE
  bbox.xmin > {west}
  AND bbox.xmax < {east}
  AND bbox.ymin > {south}
  AND bbox.ymax < {north}
;
""".format(**ac['dataswales'][0]['geometry']['bbox'])
address_query

In [ ]:
# (min_x DOUBLE, min_y DOUBLE, ma
address_query = """
SET s3_region='us-west-2';
DROP TABLE IF EXISTS adds;
CREATE TABLE adds AS 
SELECT
  * EXCLUDE geometry, -- ST_GeomFromWKB(geometry) as geom,
  ST_AsGeoJSON(ST_MakeEnvelope(bbox.xmin-0.0002, bbox.ymin-0.0002, bbox.xmax+0.0002, bbox.ymax+0.0002)) as geom
FROM
  read_parquet('s3://overturemaps-us-west-2/release/2025-04-23.0/theme=addresses/type=*/*', filename=true, hive_partitioning=1)
WHERE
  bbox.xmin > {west}
  AND bbox.xmax < {east}
  AND bbox.ymin > {south}
  AND bbox.ymax < {north}
  AND street != 'NONE';
""".format(**ac['dataswales'][0]['geometry']['bbox'])
address_query

In [ ]:
# (min_x DOUBLE, min_y DOUBLE, ma
roads_query = """
SET s3_region='us-west-2';
DROP TABLE IF EXISTS adds;
CREATE TABLE overture_roads AS 
SELECT
  * EXCLUDE geometry, ST_AsGeoJSON(ST_GeomFromWKB(geometry)) as geometry
FROM
  read_parquet('s3://overturemaps-us-west-2/release/2025-04-23.0/theme=transportation/type=segment/*', filename=true, hive_partitioning=1)
WHERE
  bbox.xmin > {west}
  AND bbox.xmax < {east}
  AND bbox.ymin > {south}
  AND bbox.ymax < {north}
  
""".format(**ac['dataswales'][0]['geometry']['bbox'])
roads_query

In [ ]:
res = duckdb.sql(obq)

In [ ]:
len(res)

In [ ]:
for row in res.fetchall():
    

In [ ]:
duckdb.sql("""select class,subclass FROM adds WHERE names.primary LIKE '%Usal%';""")

In [ ]:
duckdb.sql("select class, subclass, road_surface[1]['value'] , count(*)  from adds group by (class,subclass, road_surface[1]['value'] ) ORDER BY count(*) DESC;").fetchall()

In [ ]:
duckdb.sql("DESCRIBE adds;")

In [ ]:
annos_path = '/root/data/westport/stage/staging/addresses.geojson'
duckdb.sql("DROP TABLE IF EXISTS annos;")
duckdb.sql(f"CREATE TABLE annos AS SELECT COLUMNS('.*') AS \"annos_\\0\"  FROM ST_Read('{annos_path}');")

feat_path = '/root/data/westport/stage/staging/raw_buildings.geojson'
duckdb.sql("DROP TABLE IF EXISTS features;")
duckdb.sql(f"CREATE TABLE features AS SELECT COLUMNS('.*') AS \"features_\\0\"  FROM ST_Read('{feat_path}');")

In [ ]:
missed_sql="""
SELECT  features.* EXCLUDE features_geom, ST_AsGeoJSON(features_geom) AS geometry                                                
    FROM features LEFT JOIN annos                                                                                                    
    ON ST_Intersects(annos_geom, features_geom)                                                                                      
    WHERE annos_geom IS NULL; 
    """

In [ ]:
mr=duckdb.sql(missed_sql)

In [ ]:
mr.columns

In [ ]:
duckdb.sql("CREATE TABLE buildings AS SELECT * FROM ST_Read('/root/data/westport/stage/staging/buildings.geojson');")

In [ ]:
r=duckdb.sql(
    "SELECT *   FROM adds JOIN buildings ON ST_Intersects(adds.geom, buildings.geom);")

In [ ]:
r.fetchone()

In [ ]:
duckdb.sql(f"DROP TABLE annos")
duckdb.sql(f"CREATE TABLE annos AS SELECT COLUMNS('.*') AS \"annos_\\0\" FROM ST_Read('/root/data/scvfd/stage/ponds_anno/data_20250414_005330.json');")
duckdb.sql(f"DROP TABLE features")
duckdb.sql(f"CREATE TABLE features AS SELECT  COLUMNS('.*') AS \"features_\\0\"  FROM ST_Read('/root/data/scvfd/stage/staging/ponds.geojson');")

In [ ]:
geojoin="""
with foo AS (
    SELECT  *,ST_Distance(ST_Centroid(features_geom), ST_CEntroid(annos_geom)) as dist
    FROM features JOIN annos 
    ON ST_Intersects(annos_geom, features_geom)
    ) 
SELECT b.* EXCLUDE features_geom, ST_AsGeoJSON(b.features_geom) AS geom FROM foo AS b LEFT JOIN foo as c 
ON b.features_geom == c.features_geom AND b.dist < c.dist
WHERE c.dist IS NULL;
"""

In [ ]:
r2=duckdb.sql(geojoin)

In [ ]:
w=r2.fetchall()

In [ ]:
r2.columns

In [ ]:
r2.columns

In [ ]:
r2.columns

In [ ]:
duckdb.sql("describe table features")

In [ ]:
r=duckdb.sql(
    "SELECT * EXCLUDE (annos_geom,features_geom),ST_AsGeoJSON(features_geom) AS geometry  FROM features LEFT JOIN annos ON ST_Intersects(annos_geom, features_geom);")

In [ ]:
res=[dict(zip(r.columns, row)) for row in r.fetchall()]

In [ ]:
res

In [ ]:
fs = geojson.FeatureCollection([])
#dir(fs)

In [ ]:
features = []
for mf in res[:3]:
    f = geojson.Feature()
    for k,v	in ( (k[9:],v) for k,v in mf.items() if k.startswith('features_')):
       
        if k == 'geom':
            f['geometry'] = v
        else:
            f['properties'][k] = v
    features.append(f)
fs = geojson.FeatureCollection(features)

In [ ]:
geojson.dumps(fs, sort_keys=True)

In [ ]:
s=huh[0]['geometry']

In [ ]:
dir(duckdb)

In [ ]:
geojson.loads(s)

In [ ]:
fc = geojson.FeatureCollection()
for f in res:
    fr = geojson.Feature()
    for k,v in fr.items():
    geometry=f['features_geometry'])
    
    del(f['features_geometry'])
    del(f['annos_geometry'])
    f['properties'] = 
    

# WVFD adaptation

In [ ]:
def points_to_bbox(points):
    xset = [p[0] for p in points]
    yset = [p[1] for p in points]
    return {
        "north" : max(yset),
        "south" : min(yset),
        "east": max(xset),
        "west": min(xset),
        #"xset": xset,
        #"yset": yset
    }

roi = json.load(open("westport_runbook.geojson"))
[{'bbox': points_to_bbox(f['geometry']['coordinates'][0]),
    "name": f['properties']['Description'],
    "layers": ["hillshade", "buildings", "creeky", "roads"],
    "caption": f['properties']['Description'],
    "vectors": [], "raster": "",
     "text": f['properties']['Description'] } for f in roi['features']]

In [ ]:
roi['features'][1]

In [ ]:
#roi['features'][1]['geometry']['coordinates']
points_to_bbox(roi['features'][1]['geometry']['coordinates'][0])
points_to_bbox(roi['features'][1]['geometry']['coordinates'][0])

In [ ]:
import geopandas
geo = dc['geometry']['bbox']
geo_tuple = (geo['west'], geo['south'], geo['east'], geo['north'])
gpd = geopandas.read_file("/root/data/WVFD_clippedTA83roads2025_02_04.gpkg",
                        ).to_crs(crs=dc['crs']).clip(geo_tuple)

# Prototyping for tranlations and adaptors

In [ ]:
heli_str = """
39.3342	123.4594	
39.3325	123.4588	
		
39.3444	123.4635	
39.3414	123.4626	
		
39.3681	123.4689	Power Lines overhead
39.3595	123.4708	
39.3829	123.4714	
39.385	123.471	
39.3829	123.4714	
39.3898	123.468	
39.3944	123.4707	
39.3964	123.4709	
39.3944	123.4747	
39.396	123.467	
39.3925	123.4651	
39.7979	123.4617	
39.4074	123.4736	
39.4044	123.4739	
39.3944	123.4707	
39.3925	123.4651	616 ft ABSL
39.4044	123.4739	
39.4022	123.4677	Powerlines South of Road
39.4116	123.4756	
39.4074	123.4736	
39.4214	123.4823	Closed in Winter
39.4237	123.4825	
39.4425	123.4888	Rockport
39.4647	123.4994	
39.4503	123.4909	"""
helis=[l.split(maxsplit=2) for l in heli_str.split("\n")]

In [ ]:
def hack(s):
    deg, rest = s.split('.')
    degs = float(deg)
    badmins = float(rest)/100.0
    mins = float( rest[:2] + '.' + rest[2:])
    #secs = float(rest[2:])
    
    fdeg = degs + mins/60.0 
    #print(f"D: {degs} M: {mins} NOT {badmins} -> {fdeg}")
    return fdeg#+ secs/3600.0

hack('123.471')

In [ ]:
import geojson
def tuples_to_features(tuples):
    features = []
    for t in tuples:
        if not t:
            continue
        print(f"({t[0]}, -{t[1]}) -> (-{hack(t[1])}, {hack(t[0])})")
        f = geojson.Feature(
            geometry=geojson.Point( (-1*hack(t[1]), hack(t[0]) ) ),
            properties = {'name': t[2]} if len(t) > 2 else {}
        )
        features.append(f)
    return geojson.FeatureCollection(features)

def tsv_to_geojson(rawstring, outpath, as_string=False):
    tuples = [l.split(maxsplit=2) for l in rawstring.split("\n")]
    fc = tuples_to_features(tuples)
    if as_string:
        return geojson.dumps(fc)
    else:
        return geojson.dump(fc, open(outpath,"w"))
    

In [ ]:
tsv_to_geojson(heli_str, 'helilandings.geojson', as_string=False)

# Attic

In [ ]:
[(r['bbox']['north'] , r['bbox']['south']) for r in regions]

In [ ]:
c = json.load(open("/root/data/scvfd/staging/creeks.geojson"))
from collections import Counter
Counter([f['properties']['fcode_description'] for f in c['features']])

In [ ]:
ht1="""
            <!DOCTYPE html>

            <html>
            <head>
                <meta charset="utf-8">
                <title>Edit {name}</title>
                <script src='https://unpkg.com/maplibre-gl@3.6.2/dist/maplibre-gl.js'></script>
                <script src="https://unpkg.com/terra-draw@1.0.0-beta.0/dist/terra-draw.umd.js"></script>
                <link href='https://unpkg.com/maplibre-gl@3.6.2/dist/maplibre-gl.css' rel='stylesheet' />

                <style>
                    body {{ margin: 0; padding: 0; }}
                    #map {{ position: absolute; top: 0; bottom: 0; width: 100%; }}
                    #controls {{
                        position: absolute;
                        top: 10px;
                        right: 10px;
                        z-index: 1;
                        background: white;
                        padding: 10px;
                        border: 1px solid #ccc;
                        border-radius: 4px;
                    }}
                    #feature-text {{
                        margin-bottom: 10px;
                        padding: 5px;
                        width: 200px;
                    }}
                    #save-button {{
                        padding: 10px;
                        background: white;
                        border: 1px solid #ccc;
                        border-radius: 4px;
                        cursor: pointer;
                        width: 100%;
                    }}
                    #save-button:hover {{
                        background: #f0f0f0;
                    }}
                </style>
            </head>
            <body>
            <center>
            <h1>Edit Note Layer: {name}</h1>
            <i>Click to draw, double click to end, click "Save" button when done.</i>
            
            <A HREF="../html">cancel</a>
            </center>
            <div id="controls">
                    <input type="text" id="feature-name" placeholder="Enter name" />
                    
                    <input type="radio" id="feature-fcode_description" name="feature-fcode_description" value="Stream/River: Hydrographic Category = Intermittent" />
                    
            <button id="save-button">Save Note</button>
            </div>
            
            <div id="map"></div>
            <script>
            """
ht2="""
                var map = new maplibregl.Map({
  "container": "map",
  "style": {
    "glyphs": "https://fonts.undpgeohub.org/fonts/{fontstack}/{range}.pbf",
    "version": 8,
    "center": [
      -123.90625574273562,
      40.211
    ],
    "zoom": 12,
    "sources": {
      "hillshade": {
        "type": "image",
        "url": "../staging/hillshade.tiff.jpg",
        "coordinates": [
          [
            -123.98,
            40.26
          ],
          [
            -123.83251148547124,
            40.26
          ],
          [
            -123.83251148547124,
            40.162
          ],
          [
            -123.98,
            40.162
          ]
        ]
      },
      "roads": {
        "type": "geojson",
        "data": "/scvfd/staging/roads.geojson"
      },
      "buildings": {
        "type": "geojson",
        "data": "/scvfd/staging/buildings.geojson"
      }
    },
    "layers": [
      {
        "id": "hillshade-layer",
        "type": "raster",
        "source": "hillshade",
        "paint": {
          "raster-opacity": 1,
          "raster-contrast": 0.3
        }
      },
      {
        "id": "roads-layer",
        "type": "line",
        "source": "roads",
        "text-field": [
          "get",
          "name"
        ],
        "paint": {
          "line-color": "rgb(0, 0, 0)",
          "line-width": [
            "match",
            [
              "get",
              "STREETTYPE"
            ],
            "RD",
            5,
            "DR",
            3,
            2
          ]
        }
      },
      {
        "id": "roads-label-layer",
        "type": "symbol",
        "source": "roads",
        "layout": {
          "symbol-placement": "line",
          "text-offset": [
            0,
            2
          ],
          "text-font": [
            "Open Sans Regular"
          ],
          "text-field": [
            "get",
            "STREETNAME"
          ],
          "text-size": 20
        }
      },
      {
        "id": "buildings-layer",
        "type": "fill",
        "source": "buildings",
        "text-field": [
          "get",
          "name"
        ],
        "paint": {
          "fill-color": "rgb(200, 50, 50)"
        }
      }
    ]
  }
});
"""
ht4="""
            const td = new terraDraw.TerraDraw({{
                adapter: new terraDraw.TerraDrawMapLibreGLAdapter({{
                map: map,
                lib: maplibregl,
                }}),
                modes: [new terraDraw.TerraDrawLineStringMode()],
            }});

            // Initialize Terra Draw
            td.start();

            td.setMode("{modestring}");

            // Add save button functionality
            document.getElementById('save-button').addEventListener('click', function() {{
                const features = td.getSnapshot();
                
                {controls_string}
                // const featureText = document.getElementById('feature-text').value;
                // const vecWidth = document.getElementById('{width_att}').value;
                // const features = td.getFeatures();
                
                // Add name to each feature's properties
                features.forEach(feature => {{
                    if (!feature.properties) {{
                        feature.properties = {{}};
                    }}
                    feature.properties.text = featureText;
                    feature.properties.{width_att} = vecWidth;
                
                }});
                const geojson = {{
                    "type": "FeatureCollection",
                    "layer": "{ea['name']}",
                    "features": features
                    }};
                
                for(i = 0; i < features.length; i++){{
                    var xmlhttp = new XMLHttpRequest();   // new HttpRequest instance 
                    xmlhttp.open("POST", 'http://fireatlas.org:9998/store');
                    xmlhttp.setRequestHeader("Content-Type", "application/json");
                    var geojson_data = JSON.stringify({{"data":geojson}});
                    alert(geojson_data);
                    xmlhttp.send(geojson_data);
                    }};
                xmlhttp.onreadystatechange = function() {{
                if (xmlhttp.readyState == 4 && xmlhttp.status == 200) {{
                    alert('upload successful!');
                }} else if (xmlhttp.readyState == 4 && xmlhttp.status !== 200){{
                    alert('looks like something went wrong');
                }}
            }} }} );
            

            </script></body></html>
"""

In [ ]:
grass = '/usr/bin/grass'
sys.path.insert(
    0,subprocess.check_output([grass, "--config", "python_path"], text=True).strip())

my_env = os.environ.copy()
import grass.jupyter as gj
GRASS_LOC = dc['name']
# GRASS_LOC = GRASS_LOC_NAME + datetime.datetime.now().strftime("%I:%M%p_%B-%d-%Y")
session = gj.init("~/grassdata", GRASS_LOC, "PERMANENT")

my_env["PYTHONPATH"] = f"/usr/lib/grass83/etc/python:{my_env['PATH']}"

# TODO: ???
import grass.script as gs
    

In [ ]:
ac['outlets']['geopackage']['layers'] = []

atlas.materialize_outlet(ac, dc, ac['outlets']['geopackage'])

In [ ]:
atlas.grass_location_initialize("scvfd")

In [ ]:
atlas.build_map("scvfd")

In [ ]:
atlas.map_image("scvfd")

In [ ]:
g.crs

g2=g.to_crs("EPSG:4269")

g.explore()

# g.clip(geo_polygon).explore()
g.clip(g3).explore()

import shapely
geo = dc['geometry']['bbox']
geo_polygon = shapely.box(geo['west'], geo['south'], geo['north'], geo['east'])

from geojson import Feature, FeatureCollection,Point, Polygon
import geopandas as gpd

[(geo[x], geo[y]) for x,y in [
                ('west', 'north'), ('east', 'north'), ('east', 'south'), ('west', 'south')]
                 ]

pts=[(geo[x], geo[y]) for x,y in [
                ('west', 'north'), ('east', 'north'), ('east', 'south'), ('west', 'south')]
                 ]
fc=FeatureCollection([Feature(geometry=Polygon([pts]))])
fc

#poly = FeatureCollection([Feature(geometry=Polygon(pts))])
g3=gpd.GeoDataFrame.from_features(fc)

g3.set_crs("EPSG:4326").explore()
# EPSG:4326

g3.set_crs("EPSG:4269").explore()

del(g['quadkey'])

g.to_file("test2.geojson", driver="GeoJSON",crs='EPSG:4269', engine="fiona")

In [ ]:
ac['outlets'].keys()

In [ ]:
ac['eddies']

In [ ]:
bb=dc['geometry']['bbox']
w=(bb['east'] - bb['west'])/4.0


In [ ]:
bb['north'] - 3.0* w

In [ ]:
import matplotlib as mpl
cmap = mpl.colormaps['gist_gray']

In [ ]:
#myc=cmap.copy()

In [ ]:
import numpy as np
f=lambda x: (9.0+x)/10.0
myc = mpl.colors.ListedColormap([[f(r), f(g), f(b), a] for r,g,b,a in cmap(np.linspace(0.0,1.0, 20))])


In [ ]:
myc

In [ ]:
cmap

In [ ]:
dir(cmap)

In [ ]:
math.radians

In [ ]:
def ll2xyz(lat, long,z):
    n = 2**z
    r = math.radians(lat)
    lts = math.log(math.tan(r) + 1.0/math.cos(r))
    x = n*(0.5 + long/360)
    y = n*(1 - lts/math.pi) / 2
    return math.floor(x),math.floor(y),z

In [ ]:
ll2xyz(40.25, -123.92, 12)

In [ ]:
from fastapi import FastAPI

In [ ]:
a = FastAPI()

In [ ]:
dir(a)

In [ ]:
import fastapi
dir(fastapi.logger.logger)
#fastapi.logger.logger.handlers

fastapi.logger.logger.setLevel(0)

https://fireatlas.org/{x}/{y}/{z}.png

https://geojson.io/#new&map=12/40.228/-123.8937

In [ ]:
fastapi.logger.logger.error("HI")

In [ ]:
import logging
dir(logging)